In [177]:
from bs4 import BeautifulSoup
import requests
from bs4.element import Comment
import re
from nltk.tokenize import word_tokenize
import csv
import json
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
import pickle
import joblib

In [2]:
base_url = 'https://en.wikipedia.org'

In [4]:
# Get the links in the paragraphs for wikipedia URL
def get_links_for_url(url):
    url_title = url[url.rfind('wiki')+5:]
    print("reading page: " + url_title)
    page = requests.get(url)
    try:
        soup = BeautifulSoup(page.text, "html5lib")
        tags = soup.find_all('p')
        res_links = []
        for tag in tags:
            links = tag.find_all('a', attrs={'href': re.compile("^/wiki/")})
            for link in links:
                res_links.append(link.get('href'))
        return res_links
    except Exception as e:
        print("Error loading page")
        return None
        

In [5]:
# Get cleaned text in the paragraph for wikipedia URL
def get_text_for_url(url):
    url_title = url[url.rfind('wiki')+5:]
    print("reading page: " + url_title)
    page = requests.get(url)
    try:
        soup = BeautifulSoup(page.text, "html5lib")
        text = soup.find_all('p')
        full_text = ""
        num = 0
        for t in text:
            if num > 5:
                break
            if not t.find('img') and (t.name == 'p' or t.name == 'ul'):
                text = str(t.getText().replace('\n', ''))
                full_text += re.sub("[\(\[].*?[\)\]]", "", text) + " "
                num += 1
        return full_text
    except Exception as e:
        print("Error loading page")
        return None

In [6]:
links = get_links_for_url(base_url + '/wiki/Computer_science')
links

reading page: Computer_science


['/wiki/Process_(engineering)',
 '/wiki/Data',
 '/wiki/Computer_program',
 '/wiki/Algorithm',
 '/wiki/Data_processing',
 '/wiki/Data_storage',
 '/wiki/Communication',
 '/wiki/Digital_data',
 '/wiki/Information',
 '/wiki/Computer_scientist',
 '/wiki/Theory_of_computation',
 '/wiki/Software_design',
 '/wiki/Software_system',
 '/wiki/Practical_disciplines',
 '/wiki/Computational_complexity_theory',
 '/wiki/Computer_graphics_(computer_science)',
 '/wiki/Programming_language_theory',
 '/wiki/Computer_programming',
 '/wiki/Programming_language',
 '/wiki/Complex_systems',
 '/wiki/Human%E2%80%93computer_interaction',
 '/wiki/Computer_accessibility',
 '/wiki/Digital_computer',
 '/wiki/Abacus',
 '/wiki/Algorithm',
 '/wiki/Wilhelm_Schickard',
 '/wiki/Mechanical_calculator',
 '/wiki/Gottfried_Leibniz',
 '/wiki/Stepped_Reckoner',
 '/wiki/Charles_Xavier_Thomas',
 '/wiki/Mechanical_calculator',
 '/wiki/Arithmometer',
 '/wiki/Charles_Babbage',
 '/wiki/Difference_Engine',
 '/wiki/Analytical_Engine',
 '

In [6]:
text = get_text_for_url(base_url + '/wiki/Computer_science')
text

reading page: Computer_science


' Computer science is the study of processes that interact with data and that can be represented as data in the form of programs. It enables the use of algorithms to manipulate, store, and communicate digital information. A computer scientist studies the theory of computation and the practice of designing software systems. Its fields can be divided into theoretical and practical disciplines. Computational complexity theory is highly abstract, while computer graphics emphasizes real-world applications. Programming language theory considers approaches to the description of computational processes, while computer programming itself involves the use of programming languages and complex systems. Human–computer interaction considers the challenges in making computers useful, usable, and accessible. The earliest foundations of what would become computer science predate the invention of the modern digital computer. Machines for calculating fixed numerical tasks such as the abacus have existed 

In [21]:
def reduce(u, v):
    return (u[0].union(v[0]), u[1] + v[1])

def clean_text(text):
    if text is None:
        return None
    regex = re.compile('[^a-zA-Z ]')
    text = regex.sub(' ', text)
    tokenized_text = word_tokenize(text.lower())
    return tokenized_text


def clean_text_for_vectorizer(text):
    if text is None:
        return None
    regex = re.compile('[^a-zA-Z ]')
    text = regex.sub(' ', text)
    return text.lower()

In [9]:
def generate_representation_for_course_description(course_description, branching_factor, search_depth, representation):
    '''
    course_description: [str], string of text description for a course
    branching_factor: float, in range(0, 1), what percentage of the links we want to traverse at each step
    search_depth: the maximum depth of link traversals starting from an original word in the course_description
    
    Returns: (links, representation)
    '''
    course_description
    res = (set(), "")
    explored_urls = set()
    for word in course_description:
        url = '/wiki/' + word
        res = reduce(res, generate_representation_for_word(explored_urls, url, branching_factor, search_depth, ""))
    return res
    
    

def generate_representation_for_word(explored_urls, url, branching_factor, search_depth, representation):
    '''
    explored_urls: set, of urls that have already been explored
    url: the url we wish to find the wikipedia article on, 
    if word is multiple words, it will appear as /wiki/computer_science, /wiki/computer_graphics, etc
    branching_factor: float, in range(0, 1), which percentage of the links we want to traverse at each step
    search_depth: int, the maximum depth of link traversals starting from word
    
    return: (links, represenation)
    links: list of strings
    representation: string
    '''
    if search_depth == 0 or url in explored_urls:
        return (set(), "")
    explored_urls.add(url)
    links = get_links_for_url(base_url + url)
    if links is None: # Only if the url is not valid
        return (explored_urls, representation)
    text = get_text_for_url(base_url + url)
    representation += " " + text
    next_links = links[:min(8, int(branching_factor * len(links)))]
    
    res = (explored_urls, representation)
    for link in next_links:
        res = reduce(res, generate_representation_for_word(explored_urls, link, branching_factor, search_depth - 1, ""))
        
    return res

In [215]:
rep_for_cs_course = generate_representation_for_course_description(["Computer_science", "biology"], 0.05, 2, "")

reading page: Computer_science
reading page: Computer_science
reading page: Process_(engineering)
reading page: Process_(engineering)
reading page: Data
reading page: Data
reading page: Computer_program
reading page: Computer_program
reading page: Algorithm
reading page: Algorithm
reading page: Data_processing
reading page: Data_processing
reading page: Data_storage
reading page: Data_storage
reading page: Communication
reading page: Communication
reading page: Digital_data
reading page: Digital_data
reading page: biology
reading page: biology
reading page: Natural_science
reading page: Natural_science
reading page: Life
reading page: Life
reading page: Organism
reading page: Organism
reading page: Anatomy
reading page: Anatomy
reading page: Biochemistry
reading page: Biochemistry
reading page: Molecular_biology
reading page: Molecular_biology
reading page: Physiology
reading page: Physiology
reading page: Developmental_biology
reading page: Developmental_biology


In [216]:
rep_for_cs_course

({'/wiki/Algorithm',
  '/wiki/Anatomy',
  '/wiki/Biochemistry',
  '/wiki/Communication',
  '/wiki/Computer_program',
  '/wiki/Computer_science',
  '/wiki/Data',
  '/wiki/Data_processing',
  '/wiki/Data_storage',
  '/wiki/Developmental_biology',
  '/wiki/Digital_data',
  '/wiki/Life',
  '/wiki/Molecular_biology',
  '/wiki/Natural_science',
  '/wiki/Organism',
  '/wiki/Physiology',
  '/wiki/Process_(engineering)',
  '/wiki/biology'},
 '  Computer science is the study of processes that interact with data and that can be represented as data in the form of programs. It enables the use of algorithms to manipulate, store, and communicate digital information. A computer scientist studies the theory of computation and the practice of designing software systems. Its fields can be divided into theoretical and practical disciplines. Computational complexity theory is highly abstract, while computer graphics emphasizes real-world applications. Programming language theory considers approaches to the

In [73]:
#rep_for_Computer_science = generate_representation_for_word(set(), '/wiki/Computer_science', 0.05, 2, "")
# rep_for_Computer_science

In [22]:
with open("../../../data/courseroster/full_json.txt") as f:
    cornell_course_descriptions = json.load(f)

In [23]:
cornell_course_descriptions.keys()

dict_keys(['VIEN', 'BSOC', 'PLPPM', 'FREN', 'GREEK', 'PMA', 'AIIS', 'KOREA', 'NCC', 'CHEM', 'TURK', 'TAMIL', 'YORUB', 'MAE', 'BENGL', 'PLBIO', 'VISST', 'COMM', 'MEDVL', 'ECON', 'ENMGT', 'CHIN', 'HIST', 'PERSN', 'PUNJB', 'ORIE', 'NEPAL', 'ILRLR', 'URDU', 'BEE', 'EDUC', 'ENGRI', 'WOLOF', 'BIOG', 'HD', 'INFO', 'PSYCH', 'ENGRD', 'ARAB', 'STSCI', 'SNLIT', 'PHYS', 'PORT', 'RELST', 'ALS', 'FSAD', 'PLSCS', 'COGST', 'CZECH', 'MATH', 'NBA', 'PLHRT', 'ENTOM', 'GERST', 'JWST', 'ILRLE', 'TIBET', 'MSE', 'VETMI', 'IARD', 'PADM', 'ECE', 'BIOMI', 'TOX', 'AKKAD', 'SINHA', 'ARKEO', 'NTRES', 'SPAN', 'COLLS', 'KHMER', 'AMST', 'AEM', 'JPLIT', 'CHLIT', 'HEBRW', 'BIOMS', 'PLSCI', 'ROMS', 'ROMAN', 'PHIL', 'BIONB', 'ASTRO', 'FGSS', 'DSOC', 'BIOEE', 'ILRHR', 'VETMM', 'CAPS', 'PE', 'NACCT', 'AAS', 'ASRC', 'STS', 'JAPAN', 'MOGRK', 'KANAD', 'AIRS', 'ILROB', 'ENGRC', 'ENGL', 'HINDI', 'VTPMD', 'TECH', 'ILRIC', 'LATIN', 'SWAHL', 'BME', 'VTBMS', 'ART', 'NS', 'HADM', 'ENGRG', 'VTMED', 'ZULU', 'GRAD', 'ANSC', 'LA', 'COML

In [24]:
cornell_course_descriptions['CS'][0]

{'courseNumber': '1110',
 'courseTitle': 'Introduction to Computing Using Python',
 'description': 'Programming and problem solving using Python. Emphasizes principles of software development, style, and testing. Topics include procedures and functions, iteration, recusion, arrays and vectors, strings, an operational model of procedure and function calls, algorithms, exceptions, object-oriented programming, and GUIs (graphical user interfaces). Weekly labs provide guided practice on the computer, with staff present to help. Assignments use graphics and GUIs to help develop fluency and understanding.',
 'offered': 'Fall, Spring, Summer.',
 'outcomes': ' Be fluent in the use of procedural statements -assignments, conditional statements, loops, method calls- and  arrays. Be able to design, code, and test small Python programs that meet requirements expressed in English. This includes a basic understanding of top-down design. Understand the concepts of object-oriented programming as used i

In [186]:
corpus = []
course_codes = []
all_major_courses = [cornell_course_descriptions[key] for key in cornell_course_descriptions.keys()]
print(all_major_courses[0:100])
all_courses = []
for major_courses in all_major_courses:
    all_courses += major_courses

for i, course_data in enumerate(all_courses):
    course_number = course_data['courseNumber']
    course_title = course_data['courseTitle']
    course_desc = course_data['description']
    cleaned_course_desc = clean_text_for_vectorizer(course_desc)
    if cleaned_course_desc != None and cleaned_course_desc != []: 
        corpus.append(cleaned_course_desc)
        course_codes.append(course_data['subject'] + ' ' + course_number)
    course_outcome = None
    try:
        course_outcome = course_data['outcome']
    except Exception as e:
        course_outcome = ""

[[{'courseTitle': 'Introduction to Wines and Vines', 'subject': 'VIEN', 'professor': ['Kathy Arnink', 'Russell Moss'], 'outcomes': ' Describe the importance of fermentations to human history, health and cultures. Apply basic chemistry and biology to viticulture and enology. Explain general grape cultivation and wine production procedures. Demonstrate wine flavor evaluation and appreciation techniques.', 'description': 'Broad introduction to grape cultivation and wine fermentations. Topics include history of winemaking, viticultural regions, vineyard and winery practices, wine flavor chemistry and microbiology, and wine flavor perception. Tasting wines in class illustrates the components that determine wine quality.', 'offered': 'Fall, Spring.', 'courseNumber': '1104'}, {'courseTitle': 'Introduction to Wines and Vines Laboratory', 'subject': 'VIEN', 'professor': ['Kathy Arnink'], 'outcomes': ' Identify parts of a grapevine. Describe the process for preparing yeast & supplying proper nut

In [187]:
print(len(corpus))
print(corpus[4000])
print(len(course_codes))

4089
some of our very best evidence for roman art survives in the form of frescoes in rome  ostia and the bay of naples  exploring imperial palaces  rural villas  town houses  shops  baths  tombs  taverns and gardens  we will examine the visual dynamics and socio cultural significance of wall paintings within their original archaeological contexts  the study of frescoes offers an exciting means of tackling important questions relating to roman social history alongside the complexities of representation within the greco roman visual tradition  including the relationship between art and nature  the use of myth  the spatial dynamics of interior decorative schemes  visual verbal relations  and concepts of ornament  medium  and abstraction  this course will be taught as a traveling seminar  which will include a trip to rome and bay of naples over spring break  spaces are limited 
4089


In [179]:
vectorizer = TfidfVectorizer(lowercase= True, stop_words='english', max_df=0.7, min_df = 2, smooth_idf=True)
X = vectorizer.fit_transform(corpus)
print(X.shape)
doc_by_vocab = vectorizer.fit_transform([d for d in corpus]).toarray()

(4089, 9086)


In [89]:
def get_top_n_tfidf_terms_from_text(vectorizer, text, n):
    print("S")
    if text is None:
        return []
    feature_array = np.array(vectorizer.get_feature_names())
    transformed_text = vectorizer.transform([text])
    tfidf_sorting = np.argsort(transformed_text.toarray()).flatten()[::-1]
    k = len(text.split())
    top_n = feature_array[tfidf_sorting][:min(k, n)]
    return top_n

def get_top_n_important_terms_from_text(vectorizer, text, n):
    pass
    

In [171]:
cs4110 = "Introduction to the design of systems programs, with emphasis on multiprogrammed operating systems. Topics include concurrency, synchronization, deadlocks, memory management, protection, input-output methods, networking, file systems and security. The impact of network and distributed computing environments on operating systems is also discussed."
cs2300 = "Web programming requires the cooperation of two machines: the one in front of the viewer (client) and the one delivering the content (server). INFO 1300 concentrates almost exclusively on the client side. The main emphasis in INFO 2300 is learning about server side processing. Students begin with a short overview of the PHP server-side scripting language, then look at interactions with databases, learning about querying via the database language SQL. Through a succession of projects, students learn how to apply this understanding to the creation of an interactive, data-driven site via PHP and the MYSQL database. Also considered are technologies such as Javascript and Ajax and techniques to enhance security and privacy. Design and usability issues are emphasized. A major component of the course is the creation of a substantial web site."
cs2110 = "Intermediate programming in a high-level language and introduction to computer science. Topics include object-oriented programming (classes, objects, subclasses, types), graphical user interfaces, algorithm analysis (asymptotic complexity, big O notation), recursion, testing, program correctness (loop invariants), searching/sorting, data structures (lists, trees, stacks, queues, heaps, search trees, hash tables, graphs), graph algorithms. Java is the principal programming language."
psych1101 = "This course provides an introduction to the science of the mind.  Everyone knows what it's like to think and perceive, but this subjective experience provides little insight into how minds emerge from physical intities like brains.  To address this issue, cognitive science integrates work from at least five disciplines: Psychology, Neuroscience, Computer Science, Linguistics, and Philosophy.  This course introduces students to the insights these disciplines offer into the workings of the mind by exploring visual perception, attention, memory, learning, problem solving, language, and consciousness."
math2940 = "linear algebra and its applications  topics include matrices  determinants  vector spaces  eigenvalues and eigenvectors  orthogonality and inner product spaces  applications include brief introductions to difference equations  markov chains  and systems of linear ordinary differential equations  may include computer use in solving problems"

print(get_top_n_tfidf_terms_from_text(vectorizer, clean_text_for_vectorizer(cs2300), 15))

S
['server' 'php' 'info' 'database' 'client' 'creation' 'web' 'site'
 'usability' 'javascript' 'ajax' 'mysql' 'querying' 'viewer' 'succession']


In [182]:
from sklearn.metrics.pairwise import cosine_similarity
test_x = vectorizer.transform([cs2300])
print(test_x.shape)

res = cosine_similarity(X, test_x).flatten()
top_res = np.argsort(res)[::-1]
print(top_res[0:15])    
for res in top_res[0:15]:
    print(corpus[res])
    print("\n")

(1, 9086)
[ 719 1075 3768 2491 2558  826 1347  761 3742 3232 2989  511 3774  725
  740]
web programming requires the cooperation of two machines  the one in front of the viewer  client  and the one delivering the content  server   info      concentrates almost exclusively on the client side  the main emphasis in info      is learning about server side processing  students begin with a short overview of the php server side scripting language  then look at interactions with databases  learning about querying via the database language sql  through a succession of projects  students learn how to apply this understanding to the creation of an interactive  data driven site via php and the mysql database  also considered are technologies such as javascript and ajax and techniques to enhance security and privacy  design and usability issues are emphasized  a major component of the course is the creation of a substantial web site 


web programming requires the cooperation of two machines  the 

In [188]:
# pickle.dump(vectorizer, open("vectorizer.pkl", "wb"))
# pickle.dump(X, open("tdm.pkl", "wb"))
#pickle.dump(corpus, open("corpus.pkl", "wb"))
pickle.dump(course_codes, open("course_codes.pkl", "wb"))

In [99]:
major_codes = list(cornell_course_descriptions.keys())
print(major_codes)
all_courses = []
for major_code in major_codes:
    for course_data in cornell_course_descriptions[major_code]:
        all_courses.append(course_data)
print(len(all_courses))

['VIEN', 'BSOC', 'PLPPM', 'FREN', 'GREEK', 'PMA', 'AIIS', 'KOREA', 'NCC', 'CHEM', 'TURK', 'TAMIL', 'YORUB', 'MAE', 'BENGL', 'PLBIO', 'VISST', 'COMM', 'MEDVL', 'ECON', 'ENMGT', 'CHIN', 'HIST', 'PERSN', 'PUNJB', 'ORIE', 'NEPAL', 'ILRLR', 'URDU', 'BEE', 'EDUC', 'ENGRI', 'WOLOF', 'BIOG', 'HD', 'INFO', 'PSYCH', 'ENGRD', 'ARAB', 'STSCI', 'SNLIT', 'PHYS', 'PORT', 'RELST', 'ALS', 'FSAD', 'PLSCS', 'COGST', 'CZECH', 'MATH', 'NBA', 'PLHRT', 'ENTOM', 'GERST', 'JWST', 'ILRLE', 'TIBET', 'MSE', 'VETMI', 'IARD', 'PADM', 'ECE', 'BIOMI', 'TOX', 'AKKAD', 'SINHA', 'ARKEO', 'NTRES', 'SPAN', 'COLLS', 'KHMER', 'AMST', 'AEM', 'JPLIT', 'CHLIT', 'HEBRW', 'BIOMS', 'PLSCI', 'ROMS', 'ROMAN', 'PHIL', 'BIONB', 'ASTRO', 'FGSS', 'DSOC', 'BIOEE', 'ILRHR', 'VETMM', 'CAPS', 'PE', 'NACCT', 'AAS', 'ASRC', 'STS', 'JAPAN', 'MOGRK', 'KANAD', 'AIRS', 'ILROB', 'ENGRC', 'ENGL', 'HINDI', 'VTPMD', 'TECH', 'ILRIC', 'LATIN', 'SWAHL', 'BME', 'VTBMS', 'ART', 'NS', 'HADM', 'ENGRG', 'VTMED', 'ZULU', 'GRAD', 'ANSC', 'LA', 'COML', 'BIOAP'

In [100]:
course_representations = {}
for course_data in all_courses:
    course_number = course_data['courseNumber']
    dept = course_data['subject']
    course_desc = course_data['description']
    cleaned_course_desc = clean_text_for_vectorizer(course_desc)
    print(course_number)
    print(course_desc)
    print(cleaned_course_desc)
    top_tfidf_words = get_top_n_tfidf_terms_from_text(vectorizer, cleaned_course_desc, 20)
    print(top_tfidf_words)
    course_representation = ' '.join(top_tfidf_words)
    course_representations[dept + ' ' +str(course_number)] = course_representation
    print(course_representation)
    print("************************")

1104
Broad introduction to grape cultivation and wine fermentations. Topics include history of winemaking, viticultural regions, vineyard and winery practices, wine flavor chemistry and microbiology, and wine flavor perception. Tasting wines in class illustrates the components that determine wine quality.
broad introduction to grape cultivation and wine fermentations  topics include history of winemaking  viticultural regions  vineyard and winery practices  wine flavor chemistry and microbiology  and wine flavor perception  tasting wines in class illustrates the components that determine wine quality 
S
['wine' 'flavor' 'tasting' 'illustrates' 'wines' 'grape' 'vineyard'
 'winemaking' 'winery' 'cultivation' 'microbiology' 'determine' 'regions'
 'chemistry' 'components' 'perception' 'quality' 'broad' 'practices'
 'introduction']
wine flavor tasting illustrates wines grape vineyard winemaking winery cultivation microbiology determine regions chemistry components perception quality broad p

sensory spirits fermentation distilled samples properties different vapor enjoyment science beverages distillation liquid aging vehicle illustrate raw separation phase equilibrium
************************
4400
Uses a (bio)-chemical perspective to investigate viticulture and enological factors that impact flavor and other quality attributes (mouthfeel, color, stability) of wine and wine grapes.
uses a  bio  chemical perspective to investigate viticulture and enological factors that impact flavor and other quality attributes  mouthfeel  color  stability  of wine and wine grapes 
S
['wine' 'enological' 'mouthfeel' 'viticulture' 'flavor' 'bio' 'grapes'
 'attributes' 'color' 'stability' 'quality' 'chemical' 'factors'
 'investigate' 'uses' 'impact' 'perspective' 'explicit' 'explicitly'
 'exploit']
wine enological mouthfeel viticulture flavor bio grapes attributes color stability quality chemical factors investigate uses impact perspective explicit explicitly exploit
************************


************************
2013
Lectures and exams for this course are the same as those in PLPPM 2010. However, students in PLPPM 2013 also participate in a weekly 55-minute discussion section where they grow mushrooms and other fungi in culture, learn about contemporary classification of fungi, see examples of major taxa growing on natural substrates, and determine whether suspect pathogens really can kill agricultural crops. Students also teach their peers about the fungus world with presentations of their own creation. (CALS non-life science majors can receive college physical/life science distribution credits upon completion of this course but they must register for a letter grade. This course is also on the Arts and Sciences list of supplementary science courses and can be used to satisfy Physical and Biological Sciences distribution requirements in AS.)
lectures and exams for this course are the same as those in plppm       however  students in plppm      also participate in a wee

actor play vocal improvisation scene observation character concentration attendance imagination technique text exploring begin elements exercises training necessary performance physical
************************
2901
This studio class will introduce students to a range of contemporary performance techniques in a Spanish context.  Through exercises, improvisation, textual analysis, and scene study, students will develop core acting skills, learn relevant Spanish theatre terminology, and enhance their self-expression in Spanish.  Students will also explore the dramatic and theatrical potential of short Spanish literary texts adapted for the stage.  The course will be conducted entirely in Spanish.
this studio class will introduce students to a range of contemporary performance techniques in a spanish context   through exercises  improvisation  textual analysis  and scene study  students will develop core acting skills  learn relevant spanish theatre terminology  and enhance their self exp

This course covers the application of physical chemistry to biological systems, including spectroscopy, photochemistry, statistical mechanics, phenomena in condensed phases, electron transfer, and transport.
this course covers the application of physical chemistry to biological systems  including spectroscopy  photochemistry  statistical mechanics  phenomena in condensed phases  electron transfer  and transport 
S
['condensed' 'electron' 'spectroscopy' 'phases' 'transfer' 'transport'
 'phenomena' 'mechanics' 'chemistry' 'statistical' 'biological' 'physical'
 'application' 'covers' 'systems' 'including' 'course' 'explicitly'
 'explorations' 'explicit']
condensed electron spectroscopy phases transfer transport phenomena mechanics chemistry statistical biological physical application covers systems including course explicitly explorations explicit
************************
2900
Survey of the methods basic to the experimental study of physical chemistry, with a focus on the areas of kinetic

...

S
['extends' 'acquired' 'elementary' 'continues' 'listening' 'speaking'
 'level' 'language' 'writing' 'develop' 'reading' 'skills' 'expressing'
 'explored' 'explanation' 'explanations' 'explicit' 'explicitly' 'exploit'
 'extend']
extends acquired elementary continues listening speaking level language writing develop reading skills expressing explored explanation explanations explicit explicitly exploit extend
************************
2204
Develops conversational skill along with reading and writing skills at a High Intermediate level.
develops conversational skill along with reading and writing skills at a high intermediate level 
S
['conversational' 'skill' 'intermediate' 'develops' 'high' 'level'
 'writing' 'reading' 'skills' 'explicit' 'explicitly' 'exploit'
 'exploitation' 'exploration']
conversational skill intermediate develops high level writing reading skills explicit explicitly exploit exploitation exploration
************************
3302
Develops advanced speaking skill with

6005
This 1-credit course is designed to prepare students who have no business background for (1) legal practice in areas involving business transactions, business regulation, and/or business litigation, and (2) taking upper-level business courses such as Business Organizations, Securities Regulation, Financial Regulation, Banking, Corporate Finance, and Bankruptcy. The course is offered on an accelerated basis. The course introduces students to basic business concepts that are fundamental to business practice and to upper-level business courses, but that many students are unlikely to be familiar with if they did not major in business at the undergraduate level. In particular, the course will provide a basic introduction to the following concepts: Debt, Interest, and Present Value; Basic Business Forms (proprietorship, partnership, corporation, LLC); Capital Structure (equity, debt, and variations on the same like preferred and ABS); Basic Accounting (balance sheets, earnings statement

7589
None
None
S
[]

************************
7590
This course analyzes the structure of mortgage- and other asset-backed securities, as well as the participants in their creation, distribution, trading and regulation. The financial and legal characteristics of the underlying assets will be considered, including a basic understanding of the asset cash flows, and factors that vary those flows. Securities and Tax Law aspects of the creation, marketing and trading of these securities will be reviewed, with particular emphasis on the REMIC structure. There will be review of the secondary markets, including Government-sponsored Enterprises and "Private Label" securities issuers; the credit rating agencies; and private mortgage insurers. Lastly, there will be consideration of the laws currently governing the GSEs and what future changes they and the broader market might anticipate for those laws.
this course analyzes the structure of mortgage  and other asset backed securities  as well as th

This is a graduate seminar primarily aimed at Ph.D. students. Students will read, present, and discuss recent and classic papers in the computer security area. Outside speakers will also be invited to present current research.
this is a graduate seminar primarily aimed at ph d  students  students will read  present  and discuss recent and classic papers in the computer security area  outside speakers will also be invited to present current research 
S
['present' 'aimed' 'classic' 'invited' 'ph' 'security' 'outside'
 'primarily' 'papers' 'area' 'speakers' 'recent' 'computer' 'read'
 'discuss' 'graduate' 'students' 'current' 'seminar' 'research']
present aimed classic invited ph security outside primarily papers area speakers recent computer read discuss graduate students current seminar research
************************
7690
The Graphics/Vision Research Seminar discusses recent research in the areas of computer graphics and computer vision. The goal is to foster technical discussions an

Upon viewing Carolee Schneemann's Fuses, fellow avant-garde filmmaker Jonas Mekas proclaimed it the film of the year, saying, "It is so gorgeous… so dangerous." While Fuses was censored as pornographic, Schneemann reflects that it's lasting impact as a work of art can be attributed to how it differed from pornography, in visually conveying female pleasure: "There's no objectification or fetishization of the woman." In pushing boundaries of representation, Schneemann and her feminist cohort were considered dangerous, and they are not alone in the history of art. Female artists can be situated among other educated women in their presumptive ability to disrupt the natural (patriarchal) order of things. This course considers: women artists connoted as dangerous, from Frida Kahlo to Kara Walker; how women have been villainized in the visual record, from witches to suffragettes; and the pioneering scholars who uncover and interpret these issues, from Linda Nochlin to Deborah Willis. Ultimate

In [101]:
course_representations['CS 3410']

'memory programming computer arithmetic architectures hierarchies processor bus systems design formats assembly interface virtual hardware modes addressing sets devices software'

In [102]:
pickle.dump(course_representations, open("all_courses_20_tfidf_representations.p", "wb" ) )

In [241]:
course_representations_simple = {}
for course_data in cornell_course_descriptions['CS']:
    course_number = course_data['courseNumber']
    course_desc = course_data['description']
    cleaned_course_desc = clean_text_for_vectorizer(course_desc)
    print(course_number)
    print(course_desc)
    print(cleaned_course_desc)
    top_tfidf_words = get_top_n_tfidf_terms_from_text(vectorizer, cleaned_course_desc, 5)
    print(top_tfidf_words)
    course_representation = generate_representation_for_course_description(top_tfidf_words, 0.10, 1, "")
    course_representations_simple['CS '+str(course_number)] = course_representation
    print(course_representation)
    print("************************")

1110
Programming and problem solving using Python. Emphasizes principles of software development, style, and testing. Topics include procedures and functions, iteration, recusion, arrays and vectors, strings, an operational model of procedure and function calls, algorithms, exceptions, object-oriented programming, and GUIs (graphical user interfaces). Weekly labs provide guided practice on the computer, with staff present to help. Assignments use graphics and GUIs to help develop fluency and understanding.
programming and problem solving using python emphasizes principles of software development style and testing topics include procedures and functions iteration recusion arrays and vectors strings an operational model of procedure and function calls algorithms exceptions objectoriented programming and guis graphical user interfaces weekly labs provide guided practice on the computer with staff present to help assignments use graphics and guis to help develop fluency and understanding
S

reading page: matlab
reading page: programming
reading page: programming
reading page: conditionals
reading page: conditionals
reading page: vectorized
reading page: vectorized
reading page: constructs
reading page: constructs
({'/wiki/programming', '/wiki/constructs', '/wiki/conditionals', '/wiki/vectorized', '/wiki/matlab'}, "  MATLAB  is a multi-paradigm numerical computing environment and proprietary programming language developed by MathWorks. MATLAB allows matrix manipulations, plotting of functions and data, implementation of algorithms, creation of user interfaces, and interfacing with programs written in other languages, including C, C++, C#, Java, Fortran and Python. Although MATLAB is intended primarily for numerical computing, an optional toolbox uses the MuPAD symbolic engine, allowing access to symbolic computing abilities. An additional package, Simulink, adds graphical multi-domain simulation and model-based design for dynamic and embedded systems. As of 2018, MATLAB ha

reading page: science
reading page: mind
reading page: mind
reading page: like
reading page: like
reading page: disciplines
reading page: disciplines
reading page: intities
reading page: intities
({'/wiki/disciplines', '/wiki/intities', '/wiki/science', '/wiki/mind', '/wiki/like'}, '   Science  is a systematic enterprise that builds and organizes knowledge in the form of testable explanations and predictions about the universe. The earliest roots of science can be traced to Ancient Egypt and Mesopotamia in around 3500 to 3000 BCE. Their contributions to mathematics, astronomy, and medicine entered and shaped Greek natural philosophy of classical antiquity, whereby formal attempts were made to explain events of the physical world based on natural causes. After the fall of the Western Roman Empire, knowledge of Greek conceptions of the world deteriorated in Western Europe during the early centuries  of the Middle Ages but was preserved in the Muslim world during the Islamic Golden Age. T

reading page: shell
reading page: computational
reading page: computational
reading page: files
reading page: files
reading page: installations
reading page: installations
reading page: strings
reading page: strings
({'/wiki/shell', '/wiki/computational', '/wiki/installations', '/wiki/strings', '/wiki/files'}, ' Shell may refer to:  Computation is any type of calculation that includes both arithmetical and non-arithmetical steps and follows a well-defined model, for example an algorithm. The study of computation is paramount to the discipline of computer science. A computation can be seen as a purely physical phenomenon occurring inside a closed physical system called a computer.Examples of such physical systems include digital computers, mechanical computers, quantum computers, DNA computers, molecular computers, microfluidics-based computers, analog computers, or wetware computers.This point of view has been adopted by the physics of computation, a branch of theoretical physics, as w

reading page: php
reading page: database
reading page: database
reading page: client
reading page: client
reading page: web
reading page: web
reading page: creation
reading page: creation
({'/wiki/web', '/wiki/client', '/wiki/php', '/wiki/creation', '/wiki/database'}, '  since version 7.0: PHP: Hypertext Preprocessor  is a general-purpose programming language originally designed for web development. It was originally created by Rasmus Lerdorf in 1994; the PHP reference implementation is now produced by The PHP Group. PHP originally stood for Personal Home Page, but it now stands for the recursive initialism PHP: Hypertext Preprocessor. PHP code may be executed with a command line interface , embedded into HTML code, or it can be used in combination with various web template systems, web content management systems, and web frameworks. PHP code is usually processed by a PHP interpreter implemented as a module in a web server or as a Common Gateway Interface  executable. The web server co

...

reading page: graphics
reading page: vision
reading page: vision
reading page: computer
reading page: computer
reading page: research
reading page: research
reading page: foster
reading page: foster
({'/wiki/computer', '/wiki/graphics', '/wiki/research', '/wiki/vision', '/wiki/foster'}, ' Graphics  are visual images or designs on some surface, such as a wall, canvas, screen, paper, or stone to inform, illustrate, or entertain. In contemporary usage, it includes a pictorial representation of data, as in computer-aided design and manufacture, in typesetting and the graphic arts, and in educational and recreational software. Images that are generated by a computer are called computer graphics. Examples are photographs, drawings, Line art, graphs, diagrams, typography, numbers, symbols, geometric designs, maps, engineering drawings,or other images. Graphics often combine text, illustration, and color. Graphic design may consist of the deliberate selection, creation, or arrangement of typog

reading page: ai
reading page: workinprogress
reading page: workinprogress
reading page: emphasizing
reading page: emphasizing
reading page: researchers
reading page: researchers
reading page: results
reading page: results
({'/wiki/workinprogress', '/wiki/researchers', '/wiki/results', '/wiki/emphasizing', '/wiki/ai'}, ' AI, A.I., Ai, or ai may refer to:  Other reasons this message may be displayed:  Other reasons this message may be displayed:   Research comprises "creative and systematic work undertaken to increase the stock of knowledge, including knowledge of humans, culture and society, and the use of this stock of knowledge to devise new applications." It is used to establish or confirm facts, reaffirm the results of previous work, solve new or existing problems, support theorems, or develop new theories. A research project may also be an expansion on past work in the field. Research projects can be used to develop further knowledge on a topic, or in the example of a school resea

reading page: nlp
reading page: soon
reading page: soon
reading page: simply
reading page: simply
reading page: mandatory
reading page: mandatory
reading page: leads
reading page: leads
({'/wiki/nlp', '/wiki/soon', '/wiki/mandatory', '/wiki/simply', '/wiki/leads'}, ' NLP may refer to:  Soon may refer to:  Simply may refer to:  Mandate may refer to:  In typography, leading  refers to the distance between adjacent lines of type; however, the exact definition has become confused. In the days of hand-typesetting, it referred to the thin strips of lead that were inserted into the forms to increase the vertical distance between lines of type; in this case, the leading would be defined as the difference between 2 quantities: the size of the type and the distance from one baseline to the next. For instance, given a type size of 10\xa0points and a distance between baselines of 12\xa0points, the leading would be 2\xa0points; put another way, a leading of 2\xa0points means there is a distance of 

reading page: cryptography
reading page: discussing
reading page: discussing
reading page: classical
reading page: classical
reading page: papers
reading page: papers
reading page: recent
reading page: recent
({'/wiki/discussing', '/wiki/classical', '/wiki/recent', '/wiki/cryptography', '/wiki/papers'}, '  Cryptography or cryptology ) is the practice and study of techniques for secure communication in the presence of third parties called adversaries. More generally, cryptography is about constructing and analyzing protocols that prevent third parties or the public from reading private messages; various aspects in information security such as data confidentiality, data integrity, authentication, and non-repudiation are central to modern cryptography. Modern cryptography exists at the intersection of the disciplines of mathematics, computer science, electrical engineering, communication science, and physics. Applications of cryptography include electronic commerce, chip-based payment car

reading page: doctoral
reading page: research
reading page: research
({'/wiki/research', '/wiki/doctoral'}, ' A doctorate  or doctor\'s degree  or doctoral degree, is an academic degree awarded by universities, derived from the ancient formalism licentia docendi   In most countries, it is a research degree that qualifies the holder to teach at university level in the degree\'s field, or to work in a specific profession. There are a variety of names for doctoral degrees; the most common is the Doctor of Philosophy , which is awarded in many different fields, ranging from the humanities to scientific disciplines. In the United States and some other countries, there are also some types of vocational, technical, or professional degrees that are referred to as doctorates. Professional doctorates historically came about to meet the needs of practitioners in a variety of disciplines. However, the necessity of these degrees may vary greatly across disciplines, making their significance unclear

In [242]:
pickle.dump( course_representations_simple, open( "cs_representations_simple.p", "wb" ) )